In [90]:
import pandas as pd
import numpy as np
import pymssql
from sqlalchemy import create_engine

In [91]:
def connDatabase():
    conn = pymssql.connect(
        host='linyang5124.database.windows.net',
        user='linyang',
        password='Techlent2022',
        database='lin',
        charset='utf8'
        )
    cursor = conn.cursor(as_dict=True)
    return cursor

In [92]:
cursor = connDatabase()

In [93]:
sql_0 = 'select * from train_01_customer_campaign'
cursor.execute(sql_0)
results = cursor.fetchall()
trains = pd.DataFrame(data = results)

In [94]:
#trains

In [95]:
sql_1 = 'select * from campaign_data'
cursor.execute(sql_1)
results = cursor.fetchall()
campaign = pd.DataFrame(data = results)

In [96]:
#campaign

In [97]:
sql_2 = 'select * from customer_transaction_data'
cursor.execute(sql_2)
results = cursor.fetchall()
transaction = pd.DataFrame(data = results)

In [98]:
#transaction

In [99]:
sql_3 = 'select distinct coupon_id from coupon_item_mapping order by coupon_id'
cursor.execute(sql_3)
results = cursor.fetchall()
coupon = pd.DataFrame(data = results)

In [100]:
#coupon

In [101]:
sql_4 = 'select * from coupon_item_mapping order by coupon_id'
cursor.execute(sql_4)
results = cursor.fetchall()
coupon_item = pd.DataFrame(data = results)

In [102]:
#coupon_item

In [103]:
'''
get the sum of sales for each campaign, then merge them to train table by campaign id
'''
def getSumOfCampaign(transaction, campaign, trains):
    date_total = transaction.groupby('date', as_index=False).agg({'quantity':sum,
                                                  'selling_price':sum,
                                                  'other_discount':sum,
                                                  'coupon_discount':sum})
    #print(date_total)
    campaign_total = {}
    colunms = ['campaign_id','campaign_quantity','campaign_selling_price','campaign_other_discount', 'campaign_coupon_discount']
    for i in colunms:
        campaign_total[i] = [0]*len(campaign)
    #print(campaign_total)
    for i in range(len(campaign)):
        camp1 = campaign.iloc[i]
        camp2 = date_total[(date_total['date']>=camp1['start_date'])&(date_total['date']<=camp1['end_date'])]
        campaign_total['campaign_id'][i] = campaign.iloc[i]['campaign_id']
        campaign_total['campaign_quantity'][i] = camp2['quantity'].sum()
        campaign_total['campaign_selling_price'][i] = camp2['selling_price'].sum()
        campaign_total['campaign_other_discount'][i] = camp2['other_discount'].sum()
        campaign_total['campaign_coupon_discount'][i] = camp2['coupon_discount'].sum()
    campaign_total = pd.DataFrame(campaign_total)
    #print(campaign_total)
    trains = pd.merge(left=trains, right=campaign_total, on='campaign_id', how='left')
    #print(trains)
    return trains

In [104]:
trains_0 = getSumOfCampaign(transaction, campaign, trains)
trains_0.to_csv('trains_0.csv')

In [105]:
#trains

In [106]:
'''
get the sum of sales for each customer, then merge them to train table by customer id
'''
def getSumOfCustomer(transaction, trains):
    customer_total = transaction.groupby('customer_id', as_index=False).agg({'quantity':sum,
                                                  'selling_price':sum,
                                                  'other_discount':sum,
                                                  'coupon_discount':sum})    
    customer_total.rename(columns = {'quantity':'customer_quantity',
                                     'selling_price':'customer_selling_price',
                                     'other_discount':'customer_other_discount',
                                     'coupon_discount':'customer_coupon_discount',}, inplace=True)
    #print(customer_total)
    trains = pd.merge(left=trains, right=customer_total, on='customer_id', how='left')
    return trains

In [109]:
trains_1 = getSumOfCustomer(transaction, trains)
trains_1.to_csv('trains_1.csv')

In [110]:
#trains_1

In [111]:
'''
get the sum of sales for each coupon(includes the sum of sales for each item in this coupon), 
then merge them to train table by coupon id
'''
def getSumOfCouponByItem(transaction, coupon_item, trains):
    #coupon_total = {}
    colunms = ['coupon_id',
               'coupon_quantity',
               'coupon_selling_price',
               'coupon_other_discount', 
               'coupon_coupon_discount']
    item_total = transaction.groupby('item_id', as_index=False).agg({'quantity':sum,
                                                  'selling_price':sum,
                                                  'other_discount':sum,
                                                  'coupon_discount':sum})    
    #print(item_total)
    coupon_total_1 = pd.merge(left=coupon_item, right=item_total, on='item_id', how='left')
    #print(coupon_total_1)
    coupon_total_2 = coupon_total_1.groupby('coupon_id', as_index=False).agg({'quantity':sum,
                                                  'selling_price':sum,
                                                  'other_discount':sum,
                                                  'coupon_discount':sum})  
    coupon_total_2.rename(columns = {'quantity':'coupon_quantity',
                                     'selling_price':'coupon_selling_price',
                                     'other_discount':'coupon_other_discount',
                                     'coupon_discount':'coupon_coupon_discount',}, inplace=True)
    #print(coupon_total_2)
    trains = pd.merge(left=trains, right=coupon_total_2, on='coupon_id', how='left')
    return trains

In [112]:
trains_2 = getSumOfCouponByItem(transaction, coupon_item, trains)
trains_2.to_csv('trains_2.csv')

In [113]:
#trains_2

In [130]:
'''
get the sum of sales for each customer on the campaign
then merge them to train table by customer id
'''

def getSumOfCustomerByCampaign(transaction, campaign, trains):
    customer_campaign_total = {}
    colunms = ['id',
               'customer_campaign_quantity',
               'customer_campaign_selling_price',
               'customer_campaign_other_discount', 
               'customer_campaign_coupon_discount']
    for i in colunms:
        customer_campaign_total[i] = [0]*len(trains)
        
    first = 0
    for i in range(len(trains)):
    #for i in range(1000):
        second = i
        train_pre = trains.iloc[first]
        train = trains.iloc[i]
        
        if (train_pre['customer_id'] == train['customer_id']) and (train_pre['campaign_id'] == train['campaign_id']) and i>0:
            #print('{0} continue!'.format(i))
            customer_campaign_total['id'][i] = train['id']
            customer_campaign_total['customer_campaign_quantity'][i] = customer_campaign_total['customer_campaign_quantity'][first]
            customer_campaign_total['customer_campaign_selling_price'][i]=customer_campaign_total['customer_campaign_selling_price'][first]
            customer_campaign_total['customer_campaign_other_discount'][i]=customer_campaign_total['customer_campaign_other_discount'][first]
            customer_campaign_total['customer_campaign_coupon_discount'][i]=customer_campaign_total['customer_campaign_coupon_discount'][first]
            print('i={0}, train_id={1} done!'.format(i, train['id']))
            continue
        
        first = second
        customer_campaign = transaction[(transaction['date']>=train['start_date'])
                                        &(transaction['date']<=train['end_date'])
                                        &(transaction['customer_id']==train['customer_id'])]
        #print(customer_campaign)
        customer_campaign_total['id'][i] = trains.iloc[i]['id']
        customer_campaign_total['customer_campaign_quantity'][i] = customer_campaign['quantity'].sum()
        customer_campaign_total['customer_campaign_selling_price'][i] = customer_campaign['selling_price'].sum()
        customer_campaign_total['customer_campaign_other_discount'][i] = customer_campaign['other_discount'].sum()
        customer_campaign_total['customer_campaign_coupon_discount'][i] = customer_campaign['coupon_discount'].sum()
        #print(customer_campaign_total)
        print('i={0}, train_id={1} done!'.format(i, train['id']))
    customer_campaign_total = pd.DataFrame(customer_campaign_total)
    trains = pd.merge(left=trains, right=customer_campaign_total, on='id', how='left')
    return trains

In [131]:
trains_3 = trains.sort_values(['customer_id', 'campaign_id'])
trains_3 = getSumOfCustomerByCampaign(transaction, campaign, trains_3)

i=0, train_id=5085 done!
i=1, train_id=5380 done!
i=2, train_id=9960 done!
i=3, train_id=11262 done!
i=4, train_id=16408 done!
i=5, train_id=24063 done!
i=6, train_id=32530 done!
i=7, train_id=33151 done!
i=8, train_id=36168 done!
i=9, train_id=37226 done!
i=10, train_id=41644 done!
i=11, train_id=47528 done!
i=12, train_id=48988 done!
i=13, train_id=55285 done!
i=14, train_id=56190 done!
i=15, train_id=62237 done!
i=16, train_id=64555 done!
i=17, train_id=69667 done!
i=18, train_id=78231 done!
i=19, train_id=82987 done!
i=20, train_id=84833 done!
i=21, train_id=93767 done!
i=22, train_id=94621 done!
i=23, train_id=114549 done!
i=24, train_id=115611 done!
i=25, train_id=121542 done!
i=26, train_id=127352 done!
i=27, train_id=127409 done!
i=28, train_id=9849 done!
i=29, train_id=14264 done!
i=30, train_id=24467 done!
i=31, train_id=36239 done!
i=32, train_id=45470 done!
i=33, train_id=48771 done!
i=34, train_id=51859 done!
i=35, train_id=53230 done!
i=36, train_id=53453 done!
i=37, trai

i=300, train_id=11177 done!
i=301, train_id=11478 done!
i=302, train_id=12591 done!
i=303, train_id=35857 done!
i=304, train_id=54404 done!
i=305, train_id=61351 done!
i=306, train_id=68151 done!
i=307, train_id=70582 done!
i=308, train_id=83486 done!
i=309, train_id=86813 done!
i=310, train_id=87610 done!
i=311, train_id=89846 done!
i=312, train_id=111290 done!
i=313, train_id=122869 done!
i=314, train_id=125272 done!
i=315, train_id=607 done!
i=316, train_id=897 done!
i=317, train_id=2138 done!
i=318, train_id=3338 done!
i=319, train_id=4999 done!
i=320, train_id=5150 done!
i=321, train_id=5479 done!
i=322, train_id=13599 done!
i=323, train_id=43742 done!
i=324, train_id=44160 done!
i=325, train_id=48985 done!
i=326, train_id=49467 done!
i=327, train_id=70596 done!
i=328, train_id=73011 done!
i=329, train_id=87978 done!
i=330, train_id=88194 done!
i=331, train_id=97144 done!
i=332, train_id=97832 done!
i=333, train_id=108569 done!
i=334, train_id=114088 done!
i=335, train_id=1235 don

i=617, train_id=12666 done!
i=618, train_id=13970 done!
i=619, train_id=22326 done!
i=620, train_id=29866 done!
i=621, train_id=47705 done!
i=622, train_id=50570 done!
i=623, train_id=53875 done!
i=624, train_id=58532 done!
i=625, train_id=62910 done!
i=626, train_id=76330 done!
i=627, train_id=78167 done!
i=628, train_id=81514 done!
i=629, train_id=85118 done!
i=630, train_id=87023 done!
i=631, train_id=89354 done!
i=632, train_id=93687 done!
i=633, train_id=100619 done!
i=634, train_id=109281 done!
i=635, train_id=111478 done!
i=636, train_id=112587 done!
i=637, train_id=116839 done!
i=638, train_id=120684 done!
i=639, train_id=121132 done!
i=640, train_id=126253 done!
i=641, train_id=5825 done!
i=642, train_id=6037 done!
i=643, train_id=8248 done!
i=644, train_id=21570 done!
i=645, train_id=26077 done!
i=646, train_id=27162 done!
i=647, train_id=35373 done!
i=648, train_id=38012 done!
i=649, train_id=39052 done!
i=650, train_id=44710 done!
i=651, train_id=47060 done!
i=652, train_id

i=938, train_id=7165 done!
i=939, train_id=23649 done!
i=940, train_id=36849 done!
i=941, train_id=47392 done!
i=942, train_id=52858 done!
i=943, train_id=56700 done!
i=944, train_id=94103 done!
i=945, train_id=95487 done!
i=946, train_id=104926 done!
i=947, train_id=108255 done!
i=948, train_id=114836 done!
i=949, train_id=6749 done!
i=950, train_id=7021 done!
i=951, train_id=9315 done!
i=952, train_id=20201 done!
i=953, train_id=24708 done!
i=954, train_id=25843 done!
i=955, train_id=31415 done!
i=956, train_id=35146 done!
i=957, train_id=47798 done!
i=958, train_id=49611 done!
i=959, train_id=50220 done!
i=960, train_id=59790 done!
i=961, train_id=67474 done!
i=962, train_id=68522 done!
i=963, train_id=74763 done!
i=964, train_id=80803 done!
i=965, train_id=84364 done!
i=966, train_id=86029 done!
i=967, train_id=89276 done!
i=968, train_id=103328 done!
i=969, train_id=108790 done!
i=970, train_id=110467 done!
i=971, train_id=110987 done!
i=972, train_id=111165 done!
i=973, train_id=

i=1261, train_id=6170 done!
i=1262, train_id=7829 done!
i=1263, train_id=7831 done!
i=1264, train_id=14019 done!
i=1265, train_id=14421 done!
i=1266, train_id=16870 done!
i=1267, train_id=29134 done!
i=1268, train_id=29479 done!
i=1269, train_id=33732 done!
i=1270, train_id=36009 done!
i=1271, train_id=43410 done!
i=1272, train_id=43791 done!
i=1273, train_id=45384 done!
i=1274, train_id=46105 done!
i=1275, train_id=46530 done!
i=1276, train_id=47888 done!
i=1277, train_id=53830 done!
i=1278, train_id=57550 done!
i=1279, train_id=58104 done!
i=1280, train_id=69193 done!
i=1281, train_id=77283 done!
i=1282, train_id=78109 done!
i=1283, train_id=80606 done!
i=1284, train_id=95088 done!
i=1285, train_id=95323 done!
i=1286, train_id=97317 done!
i=1287, train_id=98676 done!
i=1288, train_id=102333 done!
i=1289, train_id=112058 done!
i=1290, train_id=112772 done!
i=1291, train_id=125512 done!
i=1292, train_id=127611 done!
i=1293, train_id=127704 done!
i=1294, train_id=6070 done!
i=1295, trai

...

i=77172, train_id=3533 done!
i=77173, train_id=6078 done!
i=77174, train_id=31624 done!
i=77175, train_id=41836 done!
i=77176, train_id=46913 done!
i=77177, train_id=50866 done!
i=77178, train_id=60401 done!
i=77179, train_id=62679 done!
i=77180, train_id=62683 done!
i=77181, train_id=67023 done!
i=77182, train_id=94072 done!
i=77183, train_id=94689 done!
i=77184, train_id=95225 done!
i=77185, train_id=114175 done!
i=77186, train_id=115734 done!
i=77187, train_id=126203 done!
i=77188, train_id=22159 done!
i=77189, train_id=24451 done!
i=77190, train_id=42157 done!
i=77191, train_id=49701 done!
i=77192, train_id=62923 done!
i=77193, train_id=67902 done!
i=77194, train_id=71324 done!
i=77195, train_id=75955 done!
i=77196, train_id=100368 done!
i=77197, train_id=107911 done!
i=77198, train_id=121702 done!
i=77199, train_id=12911 done!
i=77200, train_id=15141 done!
i=77201, train_id=27234 done!
i=77202, train_id=33104 done!
i=77203, train_id=39037 done!
i=77204, train_id=43303 done!
i=7720

i=77468, train_id=13114 done!
i=77469, train_id=20117 done!
i=77470, train_id=36084 done!
i=77471, train_id=47344 done!
i=77472, train_id=56749 done!
i=77473, train_id=56952 done!
i=77474, train_id=65043 done!
i=77475, train_id=65691 done!
i=77476, train_id=67310 done!
i=77477, train_id=69141 done!
i=77478, train_id=74369 done!
i=77479, train_id=76637 done!
i=77480, train_id=79539 done!
i=77481, train_id=89273 done!
i=77482, train_id=96290 done!
i=77483, train_id=111324 done!
i=77484, train_id=125315 done!
i=77485, train_id=16186 done!
i=77486, train_id=25125 done!
i=77487, train_id=38900 done!
i=77488, train_id=50711 done!
i=77489, train_id=52440 done!
i=77490, train_id=54226 done!
i=77491, train_id=70087 done!
i=77492, train_id=74890 done!
i=77493, train_id=76142 done!
i=77494, train_id=76656 done!
i=77495, train_id=81790 done!
i=77496, train_id=86380 done!
i=77497, train_id=97196 done!
i=77498, train_id=98971 done!
i=77499, train_id=121907 done!
i=77500, train_id=14815 done!
i=77501

i=77761, train_id=9055 done!
i=77762, train_id=9585 done!
i=77763, train_id=17307 done!
i=77764, train_id=27204 done!
i=77765, train_id=28601 done!
i=77766, train_id=29964 done!
i=77767, train_id=31018 done!
i=77768, train_id=46330 done!
i=77769, train_id=56356 done!
i=77770, train_id=67901 done!
i=77771, train_id=68028 done!
i=77772, train_id=80274 done!
i=77773, train_id=81147 done!
i=77774, train_id=83913 done!
i=77775, train_id=92845 done!
i=77776, train_id=104273 done!
i=77777, train_id=108010 done!
i=77778, train_id=112944 done!
i=77779, train_id=113823 done!
i=77780, train_id=115244 done!
i=77781, train_id=127820 done!
i=77782, train_id=21319 done!
i=77783, train_id=27798 done!
i=77784, train_id=35049 done!
i=77785, train_id=38367 done!
i=77786, train_id=47395 done!
i=77787, train_id=47510 done!
i=77788, train_id=60334 done!
i=77789, train_id=66633 done!
i=77790, train_id=66735 done!
i=77791, train_id=68830 done!
i=77792, train_id=68897 done!
i=77793, train_id=89556 done!
i=7779

i=78058, train_id=3800 done!
i=78059, train_id=3967 done!
i=78060, train_id=5556 done!
i=78061, train_id=15740 done!
i=78062, train_id=32511 done!
i=78063, train_id=42738 done!
i=78064, train_id=70958 done!
i=78065, train_id=77266 done!
i=78066, train_id=79196 done!
i=78067, train_id=85006 done!
i=78068, train_id=98928 done!
i=78069, train_id=104074 done!
i=78070, train_id=108238 done!
i=78071, train_id=5616 done!
i=78072, train_id=11068 done!
i=78073, train_id=16362 done!
i=78074, train_id=18604 done!
i=78075, train_id=20697 done!
i=78076, train_id=21402 done!
i=78077, train_id=22930 done!
i=78078, train_id=26103 done!
i=78079, train_id=27632 done!
i=78080, train_id=32767 done!
i=78081, train_id=33487 done!
i=78082, train_id=35782 done!
i=78083, train_id=37459 done!
i=78084, train_id=38158 done!
i=78085, train_id=49615 done!
i=78086, train_id=49968 done!
i=78087, train_id=53954 done!
i=78088, train_id=64652 done!
i=78089, train_id=65977 done!
i=78090, train_id=71521 done!
i=78091, tra

i=78344, train_id=949 done!
i=78345, train_id=6760 done!
i=78346, train_id=10029 done!
i=78347, train_id=12598 done!
i=78348, train_id=15132 done!
i=78349, train_id=16161 done!
i=78350, train_id=21335 done!
i=78351, train_id=26138 done!
i=78352, train_id=28849 done!
i=78353, train_id=34529 done!
i=78354, train_id=34653 done!
i=78355, train_id=42375 done!
i=78356, train_id=47546 done!
i=78357, train_id=47978 done!
i=78358, train_id=51716 done!
i=78359, train_id=51785 done!
i=78360, train_id=56600 done!
i=78361, train_id=83627 done!
i=78362, train_id=84284 done!
i=78363, train_id=91060 done!
i=78364, train_id=103994 done!
i=78365, train_id=104230 done!
i=78366, train_id=121355 done!
i=78367, train_id=122144 done!
i=78368, train_id=124625 done!


In [132]:
trains_3 = trains_3.sort_values('id')
trains_3.to_csv('trains_3.csv')

In [60]:
'''
get the sum of sales for each coupon(includes the sum of sales for each item in this coupon) on the campaign, 
then merge them to train table by coupon id
'''
# sql_5 = 'select * from coupon_item_mapping as a, item_data as b where b.item_id==a.item_id order by a.coupon_id'
# cursor.execute(sql_5)
# results = cursor.fetchall()
# coupon_item = pd.DataFrame(data = results)


def getSumOfCouponByCampaign(transaction, coupon_item, trains):
    coupon_campaign_total = {}
    colunms_1 = ['id',
               'coupon_campaign_quantity',
               'coupon_campaign_selling_price',
               'coupon_campaign_other_discount', 
               'coupon_campaign_coupon_discount']
    for i in colunms_1:
        coupon_campaign_total[i] = [0]*len(trains)
    first = 0
    for i in range(len(trains)):
    #for i in range(1000):
        second = i
        train_pre = trains.iloc[first]
        train = trains.iloc[i]
        
        if (train_pre['coupon_id'] == train['coupon_id']) and (train_pre['campaign_id'] == train['campaign_id']) and i>0:
            #print('{0} continue!'.format(i))
            coupon_campaign_total['id'][i] = train['id']
            coupon_campaign_total['coupon_campaign_quantity'][i] = coupon_campaign_total['coupon_campaign_quantity'][first]
            coupon_campaign_total['coupon_campaign_selling_price'][i]=coupon_campaign_total['coupon_campaign_selling_price'][first]
            coupon_campaign_total['coupon_campaign_other_discount'][i]=coupon_campaign_total['coupon_campaign_other_discount'][first]
            coupon_campaign_total['coupon_campaign_coupon_discount'][i]=coupon_campaign_total['coupon_campaign_coupon_discount'][first]
            print('i={0}, train_id={1} done!'.format(i, train['id']))
            continue
        
        first = second
        #print('{0} calculated!'.format(i))
                
        items = coupon_item[coupon_item['coupon_id']==train['coupon_id']]
        #print(items)
        colunms_2 = ['item_id',
               'item_campaign_quantity',
               'item_campaign_selling_price',
               'item_campaign_other_discount', 
               'item_campaign_coupon_discount']
        item_campaign_total = {}
        for j in colunms_2:
            item_campaign_total[j] = [0]*len(items)
        for j in range(len(items)):
        #for j in range(5):
            item = items.iloc[j]
            #print(item)
            item_campaign = transaction[(transaction['date']>=train['start_date'])
                                        &(transaction['date']<=train['end_date'])
                                        &(transaction['item_id']==item['item_id'])]
            if len(item_campaign)>0:
                #print(item_campaign)
                item_campaign_total['item_id'][j] = item['item_id']
                item_campaign_total['item_campaign_quantity'][j] = item_campaign['quantity'].sum()
                item_campaign_total['item_campaign_selling_price'][j] = item_campaign['selling_price'].sum()
                item_campaign_total['item_campaign_other_discount'][j] = item_campaign['other_discount'].sum()
                item_campaign_total['item_campaign_coupon_discount'][j] = item_campaign['coupon_discount'].sum()
                
        item_campaign_total = pd.DataFrame(item_campaign_total)
        #print(item_campaign_total)
        coupon_campaign_total['id'][i] = train['id']
        coupon_campaign_total['coupon_campaign_quantity'][i] = item_campaign_total['item_campaign_quantity'].sum()
        coupon_campaign_total['coupon_campaign_selling_price'][i] = item_campaign_total['item_campaign_selling_price'].sum()
        coupon_campaign_total['coupon_campaign_other_discount'][i] = item_campaign_total['item_campaign_other_discount'].sum()
        coupon_campaign_total['coupon_campaign_coupon_discount'][i] = item_campaign_total['item_campaign_coupon_discount'].sum()
        #print(coupon_campaign_total)
        print('i={0}, train_id={1} done!'.format(i, train['id']))
    coupon_campaign_total = pd.DataFrame(coupon_campaign_total)
    trains = pd.merge(left=trains, right=coupon_campaign_total, on='id', how='left')
    return trains

In [61]:
trains = trains.sort_values(['coupon_id', 'campaign_id'])
trains_4 = getSumOfCouponByCampaign(transaction, coupon_item, trains)

i=0, train_id=2191 done!
i=1, train_id=3669 done!
i=2, train_id=5269 done!
i=3, train_id=10133 done!
i=4, train_id=13450 done!
i=5, train_id=16251 done!
i=6, train_id=20183 done!
i=7, train_id=23151 done!
i=8, train_id=28482 done!
i=9, train_id=29999 done!
i=10, train_id=32181 done!
i=11, train_id=32838 done!
i=12, train_id=42646 done!
i=13, train_id=49633 done!
i=14, train_id=51598 done!
i=15, train_id=52334 done!
i=16, train_id=59957 done!
i=17, train_id=69301 done!
i=18, train_id=73756 done!
i=19, train_id=74280 done!
i=20, train_id=74487 done!
i=21, train_id=74555 done!
i=22, train_id=74807 done!
i=23, train_id=84240 done!
i=24, train_id=89601 done!
i=25, train_id=92842 done!
i=26, train_id=104866 done!
i=27, train_id=107597 done!
i=28, train_id=117136 done!
i=29, train_id=117254 done!
i=30, train_id=125029 done!
i=31, train_id=830 done!
i=32, train_id=1036 done!
i=33, train_id=4914 done!
i=34, train_id=7275 done!
i=35, train_id=12324 done!
i=36, train_id=15970 done!
i=37, train_id

i=373, train_id=154 done!
i=374, train_id=809 done!
i=375, train_id=2985 done!
i=376, train_id=4924 done!
i=377, train_id=5657 done!
i=378, train_id=5876 done!
i=379, train_id=6872 done!
i=380, train_id=7883 done!
i=381, train_id=8018 done!
i=382, train_id=8806 done!
i=383, train_id=8847 done!
i=384, train_id=9080 done!
i=385, train_id=10184 done!
i=386, train_id=10205 done!
i=387, train_id=11437 done!
i=388, train_id=11932 done!
i=389, train_id=12879 done!
i=390, train_id=13866 done!
i=391, train_id=14971 done!
i=392, train_id=15104 done!
i=393, train_id=15382 done!
i=394, train_id=17579 done!
i=395, train_id=18441 done!
i=396, train_id=18831 done!
i=397, train_id=20754 done!
i=398, train_id=28702 done!
i=399, train_id=29780 done!
i=400, train_id=29797 done!
i=401, train_id=34944 done!
i=402, train_id=37153 done!
i=403, train_id=37200 done!
i=404, train_id=37299 done!
i=405, train_id=38491 done!
i=406, train_id=40258 done!
i=407, train_id=40525 done!
i=408, train_id=40961 done!
i=409,

i=715, train_id=1266 done!
i=716, train_id=2551 done!
i=717, train_id=2778 done!
i=718, train_id=3795 done!
i=719, train_id=4565 done!
i=720, train_id=5143 done!
i=721, train_id=5648 done!
i=722, train_id=8305 done!
i=723, train_id=9160 done!
i=724, train_id=10297 done!
i=725, train_id=10380 done!
i=726, train_id=11335 done!
i=727, train_id=11690 done!
i=728, train_id=14784 done!
i=729, train_id=15892 done!
i=730, train_id=16728 done!
i=731, train_id=16960 done!
i=732, train_id=20500 done!
i=733, train_id=20947 done!
i=734, train_id=22910 done!
i=735, train_id=23315 done!
i=736, train_id=24650 done!
i=737, train_id=26185 done!
i=738, train_id=27041 done!
i=739, train_id=28171 done!
i=740, train_id=29570 done!
i=741, train_id=29812 done!
i=742, train_id=30318 done!
i=743, train_id=31871 done!
i=744, train_id=32743 done!
i=745, train_id=34547 done!
i=746, train_id=35159 done!
i=747, train_id=37513 done!
i=748, train_id=39113 done!
i=749, train_id=39159 done!
i=750, train_id=40058 done!
i

i=1067, train_id=687 done!
i=1068, train_id=3388 done!
i=1069, train_id=4366 done!
i=1070, train_id=5034 done!
i=1071, train_id=7017 done!
i=1072, train_id=8294 done!
i=1073, train_id=9257 done!
i=1074, train_id=9560 done!
i=1075, train_id=9929 done!
i=1076, train_id=10812 done!
i=1077, train_id=11573 done!
i=1078, train_id=12292 done!
i=1079, train_id=14855 done!
i=1080, train_id=15515 done!
i=1081, train_id=15521 done!
i=1082, train_id=15538 done!
i=1083, train_id=15638 done!
i=1084, train_id=17079 done!
i=1085, train_id=17376 done!
i=1086, train_id=17387 done!
i=1087, train_id=17976 done!
i=1088, train_id=21719 done!
i=1089, train_id=22068 done!
i=1090, train_id=23311 done!
i=1091, train_id=23377 done!
i=1092, train_id=26335 done!
i=1093, train_id=26992 done!
i=1094, train_id=27277 done!
i=1095, train_id=29120 done!
i=1096, train_id=32331 done!
i=1097, train_id=32955 done!
i=1098, train_id=34496 done!
i=1099, train_id=34952 done!
i=1100, train_id=35413 done!
i=1101, train_id=35491 d

i=1400, train_id=492 done!
i=1401, train_id=628 done!
i=1402, train_id=1236 done!
i=1403, train_id=2451 done!
i=1404, train_id=4849 done!
i=1405, train_id=5347 done!
i=1406, train_id=7119 done!
i=1407, train_id=7810 done!
i=1408, train_id=8865 done!
i=1409, train_id=11796 done!
i=1410, train_id=12145 done!
i=1411, train_id=12427 done!
i=1412, train_id=12641 done!
i=1413, train_id=14039 done!
i=1414, train_id=15422 done!
i=1415, train_id=16020 done!
i=1416, train_id=19454 done!
i=1417, train_id=21970 done!
i=1418, train_id=25161 done!
i=1419, train_id=25470 done!
i=1420, train_id=26119 done!
i=1421, train_id=31705 done!
i=1422, train_id=32503 done!
i=1423, train_id=33919 done!
i=1424, train_id=35320 done!
i=1425, train_id=35459 done!
i=1426, train_id=37558 done!
i=1427, train_id=37780 done!
i=1428, train_id=38072 done!
i=1429, train_id=41697 done!
i=1430, train_id=42304 done!
i=1431, train_id=44254 done!
i=1432, train_id=45350 done!
i=1433, train_id=47728 done!
i=1434, train_id=47961 do

...

i=76814, train_id=1955 done!
i=76815, train_id=10804 done!
i=76816, train_id=10903 done!
i=76817, train_id=23776 done!
i=76818, train_id=24532 done!
i=76819, train_id=25975 done!
i=76820, train_id=26746 done!
i=76821, train_id=30908 done!
i=76822, train_id=32948 done!
i=76823, train_id=33114 done!
i=76824, train_id=38992 done!
i=76825, train_id=46126 done!
i=76826, train_id=47270 done!
i=76827, train_id=56689 done!
i=76828, train_id=65597 done!
i=76829, train_id=65785 done!
i=76830, train_id=71664 done!
i=76831, train_id=78901 done!
i=76832, train_id=83177 done!
i=76833, train_id=84913 done!
i=76834, train_id=88157 done!
i=76835, train_id=101813 done!
i=76836, train_id=104329 done!
i=76837, train_id=108361 done!
i=76838, train_id=115022 done!
i=76839, train_id=119301 done!
i=76840, train_id=121947 done!
i=76841, train_id=123077 done!
i=76842, train_id=13974 done!
i=76843, train_id=34830 done!
i=76844, train_id=38448 done!
i=76845, train_id=42623 done!
i=76846, train_id=69257 done!
i=76

i=77226, train_id=1083 done!
i=77227, train_id=1635 done!
i=77228, train_id=3134 done!
i=77229, train_id=4594 done!
i=77230, train_id=5893 done!
i=77231, train_id=9298 done!
i=77232, train_id=13281 done!
i=77233, train_id=13699 done!
i=77234, train_id=13941 done!
i=77235, train_id=17484 done!
i=77236, train_id=18606 done!
i=77237, train_id=19166 done!
i=77238, train_id=19772 done!
i=77239, train_id=20658 done!
i=77240, train_id=20861 done!
i=77241, train_id=21065 done!
i=77242, train_id=21345 done!
i=77243, train_id=23075 done!
i=77244, train_id=26060 done!
i=77245, train_id=26268 done!
i=77246, train_id=31174 done!
i=77247, train_id=32697 done!
i=77248, train_id=32990 done!
i=77249, train_id=34205 done!
i=77250, train_id=35424 done!
i=77251, train_id=35741 done!
i=77252, train_id=35764 done!
i=77253, train_id=37917 done!
i=77254, train_id=38205 done!
i=77255, train_id=41686 done!
i=77256, train_id=43011 done!
i=77257, train_id=43337 done!
i=77258, train_id=43528 done!
i=77259, train_i

i=77569, train_id=1308 done!
i=77570, train_id=3932 done!
i=77571, train_id=7118 done!
i=77572, train_id=9097 done!
i=77573, train_id=14914 done!
i=77574, train_id=15768 done!
i=77575, train_id=18670 done!
i=77576, train_id=20039 done!
i=77577, train_id=20349 done!
i=77578, train_id=27107 done!
i=77579, train_id=28921 done!
i=77580, train_id=33404 done!
i=77581, train_id=33539 done!
i=77582, train_id=45856 done!
i=77583, train_id=48705 done!
i=77584, train_id=49255 done!
i=77585, train_id=50719 done!
i=77586, train_id=55064 done!
i=77587, train_id=57381 done!
i=77588, train_id=59633 done!
i=77589, train_id=71471 done!
i=77590, train_id=80275 done!
i=77591, train_id=87181 done!
i=77592, train_id=87335 done!
i=77593, train_id=89739 done!
i=77594, train_id=90872 done!
i=77595, train_id=93594 done!
i=77596, train_id=100085 done!
i=77597, train_id=2921 done!
i=77598, train_id=11866 done!
i=77599, train_id=13907 done!
i=77600, train_id=17630 done!
i=77601, train_id=23348 done!
i=77602, train

i=77875, train_id=859 done!
i=77876, train_id=3007 done!
i=77877, train_id=3318 done!
i=77878, train_id=7740 done!
i=77879, train_id=7837 done!
i=77880, train_id=8366 done!
i=77881, train_id=8388 done!
i=77882, train_id=9275 done!
i=77883, train_id=10674 done!
i=77884, train_id=12122 done!
i=77885, train_id=13175 done!
i=77886, train_id=13360 done!
i=77887, train_id=14154 done!
i=77888, train_id=15947 done!
i=77889, train_id=16866 done!
i=77890, train_id=19617 done!
i=77891, train_id=22388 done!
i=77892, train_id=22478 done!
i=77893, train_id=22925 done!
i=77894, train_id=23185 done!
i=77895, train_id=25308 done!
i=77896, train_id=26961 done!
i=77897, train_id=27746 done!
i=77898, train_id=30922 done!
i=77899, train_id=31647 done!
i=77900, train_id=32302 done!
i=77901, train_id=36096 done!
i=77902, train_id=37626 done!
i=77903, train_id=39247 done!
i=77904, train_id=39875 done!
i=77905, train_id=41152 done!
i=77906, train_id=41986 done!
i=77907, train_id=42570 done!
i=77908, train_id=4

i=78249, train_id=63 done!
i=78250, train_id=282 done!
i=78251, train_id=1501 done!
i=78252, train_id=3749 done!
i=78253, train_id=5352 done!
i=78254, train_id=5937 done!
i=78255, train_id=10997 done!
i=78256, train_id=12011 done!
i=78257, train_id=12970 done!
i=78258, train_id=13041 done!
i=78259, train_id=14331 done!
i=78260, train_id=14823 done!
i=78261, train_id=15128 done!
i=78262, train_id=17889 done!
i=78263, train_id=18231 done!
i=78264, train_id=22591 done!
i=78265, train_id=23189 done!
i=78266, train_id=23835 done!
i=78267, train_id=24795 done!
i=78268, train_id=25449 done!
i=78269, train_id=25718 done!
i=78270, train_id=25739 done!
i=78271, train_id=26586 done!
i=78272, train_id=27451 done!
i=78273, train_id=27565 done!
i=78274, train_id=27697 done!
i=78275, train_id=28730 done!
i=78276, train_id=29374 done!
i=78277, train_id=32148 done!
i=78278, train_id=33592 done!
i=78279, train_id=34401 done!
i=78280, train_id=34526 done!
i=78281, train_id=35193 done!
i=78282, train_id=3

In [66]:
trains_4 = trains_4.sort_values('id')
trains_4.to_csv('trains_4.csv')

In [40]:
#item_data = pd.read_csv('../Data/item_data.csv')
#coupon_item = pd.merge(left=coupon_item, right=item_data, on='item_id', how='left')
#item_data.head()

In [64]:
#trains = trains.sort_values(['coupon_id', 'campaign_id'])
#trains
#coupon_item
#transaction